# 1. Mining Diamond Data - Blue Nile®

## (a) Introduction
In this series of notebooks we are mining diamond data from merchants on the web, and subsequently using Machine Learning to be able to predict the price of a diamond. Diamond merchants often display data on the diamonds they are selling so people can peruse them and make a purchase online. They'll also usually have a comparison element with lots of features (the 5 C's etc.). Really though, if you're anything like me (a noob jeweller), how can you tell how the diamond is priced based on these features? I guess you'd have to take the merchants' word on it... 

What we need is data, and a regression algorithm looking at price. This notebook is the first in the series, and in it we'll tackle scraping Blue Nile® data from [their website](https://www.bluenile.com/uk/diamond-search) (soz Blue Nile... but thx for the data). 

In all seriousness, this data is the property of Blue Nile®, so please be respectful. I try and stick to web scraping best practises in these scripts, so if you are going to use it, please keep these in. They mostly revolve around slowing the functions down, which I realise may be frustrating, but let's keep to the code people.

We'll start by importing our packages and defining a couple of functions.

## (b) Import packages / define functions

In [ ]:
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns

from bs4 import BeautifulSoup
import requests
import re

from selenium import webdriver
from selenium.webdriver.common.keys import Keys
from selenium.webdriver.common.action_chains import ActionChains

import time # To help slow our functions down and time them
import random # To assign random floats to breaks, hiding predictable patterns

The below two functions are essential to working with HTML data, and we'll use these a lot throughout the notebook.

In [2]:
def pause_random(start=0.3, stop=2):
    """
    Pause the function for a random amount of time between the two integers entered.
    """
    time.sleep(random.uniform(start, stop))

In [3]:
def get_page_content(page_link):
    """
    Scrape the targeted HTML and store as a bs object
    """
    page_response = requests.get(page_link, timeout=5)
    page_content = BeautifulSoup(page_response.content)
    return(page_content)

In [4]:
def cleanhtml(raw_html):
    """
    Remove HTML tags from string.
    """
    cleanr = re.compile('<.*?>')
    cleantext = re.sub(cleanr, '', raw_html)
    return(cleantext)

## (c) Prepare Blue Nile® dataset

In this section we create a function to prepare the Blue Nile table, and do some intial exploration to help our final crawler save time.
For reference, I denote Blue Nile® as `bn` for short.

In [5]:
# For conciseness, Blue Nile we will denote as 'bn'
bn_link = 'https://www.bluenile.com/uk/diamond-search'

In [7]:
# Start web driver
browser = webdriver.Chrome('C:/Users/Edward Sims/Downloads/chromedriver.exe')
browser.get(bn_link)
pause_random()

In [8]:
def prep_bn_table(link):
    """
    Opens webdriver and prepares the table for scraping.
    """
    
    # Continue past the cookie notice if it exists
    try:
        cookie_continue = browser.find_element_by_xpath('/html/body/div[1]/button[3]')
        cookie_continue.click()
    except:
        pass

    # If the 360 view option is checked, uncheck it
    view_checkbox_status = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[4]/div[2]/div/div/div[1]/div/div')
    view_checkbox_status = str(view_checkbox_status.get_attribute('innerHTML'))
    if 'checked' in view_checkbox_status:
        view_checkbox = browser.find_element_by_class_name('bn-checkbox')
        view_checkbox.click()
        pause_random()

    # If astor option is checked, uncheck it
    astor_checkbox_status = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[5]/div[2]/div/div/div[1]/div/div')
    astor_checkbox_status = str(astor_checkbox_status.get_attribute('innerHTML'))
    if 'checked' in astor_checkbox_status:
        astor_checkbox = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[5]/div[2]/div/div')
        astor_checkbox.click()
        pause_random()
        
    # If more filters is unselected, select it    
    filter_status = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[13]/span')
    filter_status = str(filter_status.get_attribute('innerHTML'))
    if 'More' in filter_status:
        more_filters = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[13]')
        more_filters.click()
    
    # Add extra options if they are not already added
    polish_add = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[12]/div[1]/div[1]/div/div')
    symmetry_add = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[12]/div[2]/div[1]/div/div')
    fluorescence_add = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[12]/div[3]/div[1]/div/div')
    depth_add = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[12]/div[4]/div[1]/div/div')
    table_add = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[12]/div[5]/div[1]/div/div')
    lw_add = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[12]/div[6]/div[1]/div/div')
    
    feature_add_all = [polish_add, symmetry_add, fluorescence_add, depth_add, table_add, lw_add]
    for feature_add in feature_add_all:
        if 'toggled' not in str(feature_add.get_attribute('outerHTML')):
            feature_add.click()
            pause_random()
            
    culet_add = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[12]/div[8]/div[2]/button')
    if 'active' not in str(culet_add.get_attribute('outerHTML')):
        culet_add.click()
        pause_random()
    
    # Add in all types of shape
    round_details = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[6]/div[2]/div/div[1]/div[3]')
    princess_details = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[6]/div[2]/div/div[2]/div[3]')
    emerald_details = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[6]/div[2]/div/div[3]/div[3]')
    asscher_details = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[6]/div[2]/div/div[4]/div[3]')
    cushion_details = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[6]/div[2]/div/div[5]/div[3]')
    marquise_details = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[6]/div[2]/div/div[6]/div[3]')
    radiant_details = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[6]/div[2]/div/div[7]/div[3]')
    oval_details = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[6]/div[2]/div/div[8]/div[3]')
    pear_details = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[6]/div[2]/div/div[9]/div[3]')
    heart_details = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[6]/div[2]/div/div[10]/div[3]')
    
    shape_details_all = [round_details, princess_details, emerald_details, asscher_details, cushion_details, 
                         marquise_details, radiant_details, oval_details, pear_details, heart_details]
    
    for shape_details in shape_details_all:
        if 'selected' not in str(shape_details.get_attribute('outerHTML')):
            shape_details.click()
            pause_random()

In [9]:
# Open and prepare the bn table for scraping
prep_bn_table(bn_link)

The difficulty with scraping the table is that a maximum of 1,000 results are displayed. And the prices of diamonds are hugely skewed around the £600-£2,000 price range. Now we could just increase the price range by a small amount, say, £10 at a time, but given that the maximum price is over a million, this will end up taking FOREVER. But what's more, is that even in that price range there are still sometimes too many records for the table to display. And even worse still, because the data are so skewed, we'll be looping through prices at the higher end and there will not even be anything in there to display. So basically a massive waste of time for everybody involved.

What we'll do instead is do a bit of exploration first.

The below will loop through price ranges and scrape the numbers of results in each interval, so we can gain a rough picture of the distribution of our dataset. This will take a little time, but should help us cut down the time our final looping function takes. 

N.B. This took ~30mins to complete.

In [28]:
def collect_price_freqs():
    """
    Loops through price, scrapes and stores the 
    number of results at each range.
    """
    
    def get_num_results():
        """
        Scrapes the number of results shown in the price range.    
        """
        results_path = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[2]/div[4]/button[1]/span[2]')
        # Scrape the HTML and clean
        results_val = cleanhtml(str(BeautifulSoup(results_path.get_attribute('innerHTML'))))
        # Strip the punctuation, and convert to integer
        results_val = int(re.sub(r'[^\w\s]','', results_val))
        return(results_val)

    # Create a dataframe with our new headers
    headers = ['price_range','freq']
    bn_price_freq = pd.DataFrame(columns=headers)
    
    # Min and max price locations
    min_price_box = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[7]/div[2]/div/div[1]/input[1]')
    max_price_box = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[7]/div[2]/div/div[1]/input[2]')
    
    # Assign a default interval value
    price_interval = 10000
    
    # Get the min and max values (without £ and comma values)
    min_price_value = int(min_price_box.get_attribute('value')[1:].replace(',', ''))
    min_price_value = min_price_value - 1 # Minus 1, so we can add 1 in the loop
    max_price_value = int(max_price_box.get_attribute('value')[1:].replace(',', ''))
    
    # Find a neutral zone to click on
    neutral = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[7]/div[1]/h3')
    
    start = time.time()
    # Loop through prices and store
    for min_val in range(min_price_value, max_price_value, price_interval):
        
        lower_price = min_val + 1 # Add 1 so there are no overlapping intervals
        higher_price = min_val + price_interval
        
        # Edit max price
        max_price_box.click()
        max_price_box.send_keys(Keys.BACKSPACE)
        max_price_box.send_keys(str(higher_price)) 
        neutral.click()
        time.sleep(random.uniform(0.3,2))
        
        # Edit min price            
        min_price_box.click()
        min_price_box.send_keys(Keys.BACKSPACE)
        min_price_box.send_keys(str(lower_price))
        neutral.click()
        time.sleep(random.uniform(0.3,1))               
        
        # Store the range and keep going
        price_range = str(lower_price) + ' to ' + str(higher_price)
        freq = get_num_results()
        results = [price_range, freq]
        
        bn_price_freq = bn_price_freq.append(dict(zip(headers,results)),ignore_index=True)
        
        
    end = time.time()
    print(end - start, 'secs to complete')
    return(bn_price_freq)

In [30]:
# Collect the frequencies and remove all ranges with no results
bn_price_freqs = collect_price_freqs()
bn_price_freqs.head()

586.6517744064331 secs to complete


price_range    freq
0    213 to 10212  197611
1  10213 to 20212   10469
2  20213 to 30212    3158
3  30213 to 40212    1552
4  40213 to 50212     935

In [31]:
bn_price_freqs = pd.read_csv('bn_price_freqs.csv')

In [32]:
len(bn_price_freqs)

777

In [78]:
int_range_list = []
for int_range in bn_price_freqs['price_range']:
    int_range_list.append(int_range.split(' to '))
    for int_range in int_range_list:
        print(int_range)

['201', '2200']
['201', '2200']
['2201', '4200']
['201', '2200']
['2201', '4200']
['4201', '6200']
['201', '2200']
['2201', '4200']
['4201', '6200']
['6201', '8200']
['201', '2200']
['2201', '4200']
['4201', '6200']
['6201', '8200']
['8201', '10200']
['201', '2200']
['2201', '4200']
['4201', '6200']
['6201', '8200']
['8201', '10200']
['10201', '12200']
['201', '2200']
['2201', '4200']
['4201', '6200']
['6201', '8200']
['8201', '10200']
['10201', '12200']
['12201', '14200']
['201', '2200']
['2201', '4200']
['4201', '6200']
['6201', '8200']
['8201', '10200']
['10201', '12200']
['12201', '14200']
['14201', '16200']
['201', '2200']
['2201', '4200']
['4201', '6200']
['6201', '8200']
['8201', '10200']
['10201', '12200']
['12201', '14200']
['14201', '16200']
['16201', '18200']
['201', '2200']
['2201', '4200']
['4201', '6200']
['6201', '8200']
['8201', '10200']
['10201', '12200']
['12201', '14200']
['14201', '16200']
['16201', '18200']
['18201', '20200']
['201', '2200']
['2201', '4200']
['4201

['104201', '106200']
['106201', '108200']
['108201', '110200']
['110201', '112200']
['112201', '114200']
['114201', '116200']
['116201', '118200']
['118201', '120200']
['120201', '122200']
['122201', '124200']
['124201', '126200']
['126201', '128200']
['128201', '130200']
['130201', '132200']
['201', '2200']
['2201', '4200']
['4201', '6200']
['6201', '8200']
['8201', '10200']
['10201', '12200']
['12201', '14200']
['14201', '16200']
['16201', '18200']
['18201', '20200']
['20201', '22200']
['22201', '24200']
['24201', '26200']
['26201', '28200']
['28201', '30200']
['30201', '32200']
['32201', '34200']
['34201', '36200']
['36201', '38200']
['38201', '40200']
['40201', '42200']
['42201', '44200']
['44201', '46200']
['46201', '48200']
['48201', '50200']
['50201', '52200']
['52201', '54200']
['54201', '56200']
['56201', '58200']
['58201', '60200']
['60201', '62200']
['62201', '64200']
['64201', '66200']
['66201', '68200']
['68201', '70200']
['70201', '72200']
['72201', '74200']
['74201', '76

['20201', '22200']
['22201', '24200']
['24201', '26200']
['26201', '28200']
['28201', '30200']
['30201', '32200']
['32201', '34200']
['34201', '36200']
['36201', '38200']
['38201', '40200']
['40201', '42200']
['42201', '44200']
['44201', '46200']
['46201', '48200']
['48201', '50200']
['50201', '52200']
['52201', '54200']
['54201', '56200']
['56201', '58200']
['58201', '60200']
['60201', '62200']
['62201', '64200']
['64201', '66200']
['66201', '68200']
['68201', '70200']
['70201', '72200']
['72201', '74200']
['74201', '76200']
['76201', '78200']
['78201', '80200']
['80201', '82200']
['82201', '84200']
['84201', '86200']
['86201', '88200']
['88201', '90200']
['90201', '92200']
['92201', '94200']
['94201', '96200']
['96201', '98200']
['98201', '100200']
['100201', '102200']
['102201', '104200']
['104201', '106200']
['106201', '108200']
['108201', '110200']
['110201', '112200']
['112201', '114200']
['114201', '116200']
['116201', '118200']
['118201', '120200']
['120201', '122200']
['122201

['182201', '184200']
['184201', '186200']
['186201', '188200']
['188201', '190200']
['190201', '192200']
['192201', '194200']
['194201', '196200']
['196201', '198200']
['198201', '200200']
['200201', '202200']
['202201', '204200']
['204201', '206200']
['206201', '208200']
['208201', '210200']
['210201', '212200']
['212201', '214200']
['214201', '216200']
['216201', '218200']
['218201', '220200']
['220201', '222200']
['201', '2200']
['2201', '4200']
['4201', '6200']
['6201', '8200']
['8201', '10200']
['10201', '12200']
['12201', '14200']
['14201', '16200']
['16201', '18200']
['18201', '20200']
['20201', '22200']
['22201', '24200']
['24201', '26200']
['26201', '28200']
['28201', '30200']
['30201', '32200']
['32201', '34200']
['34201', '36200']
['36201', '38200']
['38201', '40200']
['40201', '42200']
['42201', '44200']
['44201', '46200']
['46201', '48200']
['48201', '50200']
['50201', '52200']
['52201', '54200']
['54201', '56200']
['56201', '58200']
['58201', '60200']
['60201', '62200']
[

['134201', '136200']
['136201', '138200']
['138201', '140200']
['140201', '142200']
['142201', '144200']
['144201', '146200']
['146201', '148200']
['148201', '150200']
['150201', '152200']
['152201', '154200']
['154201', '156200']
['156201', '158200']
['158201', '160200']
['160201', '162200']
['162201', '164200']
['164201', '166200']
['166201', '168200']
['168201', '170200']
['170201', '172200']
['172201', '174200']
['174201', '176200']
['176201', '178200']
['178201', '180200']
['180201', '182200']
['182201', '184200']
['184201', '186200']
['186201', '188200']
['188201', '190200']
['190201', '192200']
['192201', '194200']
['194201', '196200']
['196201', '198200']
['198201', '200200']
['200201', '202200']
['202201', '204200']
['204201', '206200']
['206201', '208200']
['208201', '210200']
['210201', '212200']
['212201', '214200']
['214201', '216200']
['216201', '218200']
['218201', '220200']
['220201', '222200']
['222201', '224200']
['224201', '226200']
['226201', '228200']
['228201', '2

...

['392201', '394200']
['394201', '396200']
['396201', '398200']
['398201', '400200']
['400201', '402200']
['402201', '404200']
['404201', '406200']
['406201', '408200']
['408201', '410200']
['410201', '412200']
['412201', '414200']
['414201', '416200']
['416201', '418200']
['418201', '420200']
['420201', '422200']
['422201', '424200']
['424201', '426200']
['426201', '428200']
['428201', '430200']
['430201', '432200']
['432201', '434200']
['434201', '436200']
['436201', '438200']
['438201', '440200']
['440201', '442200']
['442201', '444200']
['444201', '446200']
['446201', '448200']
['448201', '450200']
['450201', '452200']
['452201', '454200']
['454201', '456200']
['456201', '458200']
['458201', '460200']
['460201', '462200']
['462201', '464200']
['464201', '466200']
['466201', '468200']
['468201', '470200']
['470201', '472200']
['472201', '474200']
['474201', '476200']
['476201', '478200']
['478201', '480200']
['480201', '482200']
['482201', '484200']
['484201', '486200']
['486201', '4

['814201', '816200']
['816201', '818200']
['818201', '820200']
['820201', '822200']
['822201', '824200']
['824201', '826200']
['826201', '828200']
['828201', '830200']
['830201', '832200']
['832201', '834200']
['834201', '836200']
['836201', '838200']
['838201', '840200']
['840201', '842200']
['842201', '844200']
['844201', '846200']
['846201', '848200']
['848201', '850200']
['850201', '852200']
['852201', '854200']
['854201', '856200']
['856201', '858200']
['858201', '860200']
['860201', '862200']
['862201', '864200']
['864201', '866200']
['866201', '868200']
['868201', '870200']
['870201', '872200']
['872201', '874200']
['874201', '876200']
['876201', '878200']
['878201', '880200']
['880201', '882200']
['882201', '884200']
['884201', '886200']
['886201', '888200']
['888201', '890200']
['890201', '892200']
['892201', '894200']
['894201', '896200']
['896201', '898200']
['898201', '900200']
['900201', '902200']
['902201', '904200']
['904201', '906200']
['906201', '908200']
['908201', '9

['1216201', '1218200']
['1218201', '1220200']
['1220201', '1222200']
['1222201', '1224200']
['1224201', '1226200']
['1226201', '1228200']
['1228201', '1230200']
['1230201', '1232200']
['1232201', '1234200']
['1234201', '1236200']
['1236201', '1238200']
['1238201', '1240200']
['1240201', '1242200']
['1242201', '1244200']
['1244201', '1246200']
['1246201', '1248200']
['1248201', '1250200']
['1250201', '1252200']
['1252201', '1254200']
['1254201', '1256200']
['1256201', '1258200']
['1258201', '1260200']
['1260201', '1262200']
['1262201', '1264200']
['1264201', '1266200']
['1266201', '1268200']
['1268201', '1270200']
['1270201', '1272200']
['1272201', '1274200']
['1274201', '1276200']
['1276201', '1278200']
['1278201', '1280200']
['1280201', '1282200']
['1282201', '1284200']
['1284201', '1286200']
['1286201', '1288200']
['1288201', '1290200']
['1290201', '1292200']
['1292201', '1294200']
['1294201', '1296200']
['1296201', '1298200']
['1298201', '1300200']
['1300201', '1302200']
['1302201',

['60201', '62200']
['62201', '64200']
['64201', '66200']
['66201', '68200']
['68201', '70200']
['70201', '72200']
['72201', '74200']
['74201', '76200']
['76201', '78200']
['78201', '80200']
['80201', '82200']
['82201', '84200']
['84201', '86200']
['86201', '88200']
['88201', '90200']
['90201', '92200']
['92201', '94200']
['94201', '96200']
['96201', '98200']
['98201', '100200']
['100201', '102200']
['102201', '104200']
['104201', '106200']
['106201', '108200']
['108201', '110200']
['110201', '112200']
['112201', '114200']
['114201', '116200']
['116201', '118200']
['118201', '120200']
['120201', '122200']
['122201', '124200']
['124201', '126200']
['126201', '128200']
['128201', '130200']
['130201', '132200']
['132201', '134200']
['134201', '136200']
['136201', '138200']
['138201', '140200']
['140201', '142200']
['142201', '144200']
['144201', '146200']
['146201', '148200']
['148201', '150200']
['150201', '152200']
['152201', '154200']
['154201', '156200']
['156201', '158200']
['158201',

['420201', '422200']
['422201', '424200']
['424201', '426200']
['426201', '428200']
['428201', '430200']
['430201', '432200']
['432201', '434200']
['434201', '436200']
['436201', '438200']
['438201', '440200']
['440201', '442200']
['442201', '444200']
['444201', '446200']
['446201', '448200']
['448201', '450200']
['450201', '452200']
['452201', '454200']
['454201', '456200']
['456201', '458200']
['458201', '460200']
['460201', '462200']
['462201', '464200']
['464201', '466200']
['466201', '468200']
['468201', '470200']
['470201', '472200']
['472201', '474200']
['474201', '476200']
['476201', '478200']
['478201', '480200']
['480201', '482200']
['482201', '484200']
['484201', '486200']
['486201', '488200']
['488201', '490200']
['490201', '492200']
['492201', '494200']
['494201', '496200']
['496201', '498200']
['498201', '500200']
['500201', '502200']
['502201', '504200']
['504201', '506200']
['506201', '508200']
['508201', '510200']
['510201', '512200']
['512201', '514200']
['514201', '5

In [ ]:
bn_price_freqs_no_zero = bn_price_freqs[bn_price_freqs.freq != 0]
bn_price_freqs_no_zero = bn_price_freqs_no_zero.reindex(index=bn_price_freqs_no_zero.index[::-1]).reset_index(drop=True)

In [ ]:
bn_price_freqs_no_zero

We'll gather all the final values into one larger bin to save some time there. Let's see how far we can go from the maximum before it gets over 900.

In [ ]:
freq = 0
max_val = bn_price_freqs_no_zero.iloc[0,0].split(' to ')[1]
for index, freq_val in bn_price_freqs_no_zero.iterrows():
    if freq >= 900:
        #max_val = freq_val[0].split(' to ')[1]
        print(freq_val[0].split(' to ')[0], 'to', max_val, ':\t', freq)
        freq = 0

        
    freq = freq + freq_val[1]

In that case, we'll iterate through prices up to £6,000 in £5 increments, up to £12,200 in £200 increments, up to £20,200 in £500 increments, up to £98,200 in £2,000 increments, and straight to the max from £19,201. Hopefully that'll make things a little easier on the Blue Nile servers, and not leave me waiting for decades for the algorithm to finish.

In [ ]:
def get_bn_data():
    """
    Loops through all the price values, scrapes the results and stores
    it into a dataframe.
    """
    
    def get_num_results():
        """
        Scrapes the number of results shown in the price range.    
        """
        results_path = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[2]/div[4]/button[1]/span[2]')
        # Scrape the HTML and clean
        results_val = cleanhtml(str(BeautifulSoup(results_path.get_attribute('innerHTML'))))
        # Strip the punctuation, and convert to integer
        results_val = int(re.sub(r'[^\w\s]','', results_val))
        return(results_val)    
    
    bn_headers = []
    
    # Isolate the table headers HTML
    headers_data = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/section/div/div/div[1]/div')
    headers_html = BeautifulSoup(headers_data.get_attribute('innerHTML'))
    
    # Get the header values
    for div in headers_html.find_all('div'):
        for header in div.find_all('span'):
            bn_headers.append(cleanhtml(str(header)))
    bn_headers = list(filter(('').__ne__, bn_headers))
    bn_headers.remove('Compare')
    
    # Create a dataframe with our new headers
    bn_df = pd.DataFrame(columns=bn_headers)
    
    # Min and max price locations
    min_price_box = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[7]/div[2]/div/div[1]/input[1]')
    max_price_box = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[7]/div[2]/div/div[1]/input[2]')
    
    
    # Assign a default range value
    price_range = 5
    
    # Get the min and max values (without £ and comma values)
    min_price_value = int(min_price_box.get_attribute('value')[1:].replace(',', ''))
    max_price_value = int(max_price_box.get_attribute('value')[1:].replace(',', ''))
    
    # Find a neutral zone to click on
    neutral = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/div[1]/div[2]/div[3]/div[7]/div[1]/h3')
    
    ####### EDITS HERE ########        

    def bn_table_scrape_loop(price_range):
        
        # Loop through prices to limit numbers displayed
        for min_val in range(min_price_value, max_price_value, price_range):   
            # Edit min price
            min_price_box.click()
            min_price_box.send_keys(Keys.BACKSPACE)
            min_price_box.send_keys(str(min_val))
            neutral.click()
            time.sleep(random.uniform(0.3,2))
            
            # Edit max price
            max_price_box.click()
            max_price_box.send_keys(Keys.BACKSPACE)
            time.sleep(2)
            max_price_box.send_keys(str(min_val+price_range)) 
            neutral.click()
    
            time.sleep(random.uniform(0.3,2))
            
            table_web_source = browser.find_element_by_xpath('//*[@id="react-app"]/div/div/div/section[1]/section/div/div/div[2]')
            table_html = BeautifulSoup(table_web_source.get_attribute('innerHTML'))
            
            # Scrape the table! First get the raw table html
            table_rows_html = table_html.find_all('a',{'class':'grid-row row '})
            time.sleep(random.uniform(0.3,3))
                
            # Then loop through each row 
            for row in table_rows_html:
                bn_data = []
                # And loop through each value
                for value in row.find_all('span'):
                    bn_data.append(cleanhtml(str(value)))
                
                bn_data = list(filter(('').__ne__, bn_data)) # Remove all empty values
                del bn_data[4] # Delete index 4 in list as it returns two dupe vals - unique to their HTML
                #print(bn_data)
                bn_df = bn_df.append(dict(zip(bn_headers,bn_data)),ignore_index=True)

    
        return(bn_df)

In [ ]:
get_bn_data()

In [ ]:
for min_val in range(0, 100, 5):
    if min_val <= 20:
        print(5)
    elif min_val <= 60:
        print(20)
    else:
        print(40)